# Incidence of influenza-like illness in France

In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

The data on the incidence of influenza-like illness are available from the Web site of the [Réseau Sentinelles](http://www.sentiweb.fr/). We download them as a file in CSV format, in which each line corresponds to a week in the observation period. Only the complete dataset, starting in 1984 and ending with a recent week, is available for download.

In [2]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-3.csv"

This is the documentation of the data from [the download site](https://ns.sentiweb.fr/incidence/csv-schema-v1.json):

| Column name  | Description                                                                                                               |
|--------------|---------------------------------------------------------------------------------------------------------------------------|
| `week`       | ISO8601 Yearweek number as numeric (year times 100 + week nubmer)                                                               |
| `indicator`  | Unique identifier of the indicator, see metadata document https://www.sentiweb.fr/meta.json                               |
| `inc`        | Estimated incidence value for the time step, in the geographic level                                                      |
| `inc_low`    | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc_up`     | Upper bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100`     | Estimated rate incidence per 100,000 inhabitants                                                                          |
| `inc100_low` | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100_up`  | Upper bound of the estimated rate incidence 95% Confidence Interval                                                       |
| `geo_insee`  | Identifier of the geographic area, from INSEE https://www.insee.fr                                                        |
| `geo_name`   | Geographic label of the area, corresponding to INSEE code. This label is not an id and is only provided for human reading |

The first line of the CSV file is a comment, which we ignore with `skip=1`.

In [8]:
raw_data = pd.read_csv(data_file, skiprows=1)
raw_data.head(5)

week  indicator     inc   inc_low    inc_up inc100  inc100_low  \
0  202407          3  163687  148996.0  178378.0    245       223.0   
1  202406          3  191550  179309.0  203791.0    287       269.0   
2  202405          3  216237  203595.0  228879.0    324       305.0   
3  202404          3  213196  200547.0  225845.0    320       301.0   
4  202403          3  163457  152276.0  174638.0    245       228.0   

   inc100_up geo_insee geo_name  
0      267.0        FR   France  
1      305.0        FR   France  
2      343.0        FR   France  
3      339.0        FR   France  
4      262.0        FR   France

Are there missing data points? Yes, week 19 of year 1989 does not have any observed values.

In [5]:
raw_data[raw_data.isnull().any(axis=1)]

week  indicator inc  inc_low  inc_up inc100  inc100_low  inc100_up  \
1814  198919          3   -      NaN     NaN      -         NaN        NaN   

     geo_insee geo_name  
1814        FR   France

We delete this point, which does not have big consequence for our rather simple analysis.

In order to protect us in case the Réseau Sentinelles Web server disappears or is modified, we make a local copy of this dataset that we store together with our analysis. It is unnecessary and even risky to download the data at each execution, because in case of a malfunction we might be replacing our file by a corrupted version. Therefore we download the data only if no local copy exists.

In [6]:
data_file = "syndrome-grippal.csv"

import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

In [7]:
data = raw_data.dropna().copy()
data

week  indicator     inc   inc_low    inc_up inc100  inc100_low  \
0     202407          3  163687  148996.0  178378.0    245       223.0   
1     202406          3  191550  179309.0  203791.0    287       269.0   
2     202405          3  216237  203595.0  228879.0    324       305.0   
3     202404          3  213196  200547.0  225845.0    320       301.0   
4     202403          3  163457  152276.0  174638.0    245       228.0   
5     202402          3  129436  119453.0  139419.0    194       179.0   
6     202401          3  120769  109452.0  132086.0    181       164.0   
7     202352          3  115446  103738.0  127154.0    174       156.0   
8     202351          3  148755  136546.0  160964.0    224       206.0   
9     202350          3  147971  136787.0  159155.0    223       206.0   
10    202349          3  147552  136422.0  158682.0    222       205.0   
11    202348          3  124204  113479.0  134929.0    187       171.0   
12    202347          3  110910  100658.0  121162.0    167       152.0   
13    202346          3   83853   75096.0   92610.0    126       113.0   
14    202345          3   72003   63178.0   80828.0    108        95.0   
15    202344          3   49952   42813.0   57091.0     75        64.0   
16    202343          3   44982   38170.0   51794.0     68        58.0   
17    202342          3   56842   49277.0   64407.0     86        75.0   
18    202341          3   58357   51032.0   65682.0     88        77.0   
19    202340          3   68894   60069.0   77719.0    104        91.0   
20    202339          3   72003   63452.0   80554.0    108        95.0   
21    202338          3   63218   55227.0   71209.0     95        83.0   
22    202337          3   49085   42079.0   56091.0     74        63.0   
23    202336          3   38247   32237.0   44257.0     58        49.0   
24    202335          3   31695   26013.0   37377.0     48        39.0   
25    202334          3   26663   21057.0   32269.0     40        32.0   
26    202333          3   19144   13161.0   25127.0     29        20.0   
27    202332          3   14641   10285.0   18997.0     22        15.0   
28    202331          3   15286   10705.0   19867.0     23        16.0   
29    202330          3   13205    8647.0   17763.0     20        13.0   
...      ...        ...     ...       ...       ...    ...         ...   
2021  198521          3   26096   19621.0   32571.0     47        35.0   
2022  198520          3   27896   20885.0   34907.0     51        38.0   
2023  198519          3   43154   32821.0   53487.0     78        59.0   
2024  198518          3   40555   29935.0   51175.0     74        55.0   
2025  198517          3   34053   24366.0   43740.0     62        44.0   
2026  198516          3   50362   36451.0   64273.0     91        66.0   
2027  198515          3   63881   45538.0   82224.0    116        83.0   
2028  198514          3  134545  114400.0  154690.0    244       207.0   
2029  198513          3  197206  176080.0  218332.0    357       319.0   
2030  198512          3  245240  223304.0  267176.0    445       405.0   
2031  198511          3  276205  252399.0  300011.0    501       458.0   
2032  198510          3  353231  326279.0  380183.0    640       591.0   
2033  198509          3  369895  341109.0  398681.0    670       618.0   
2034  198508          3  389886  359529.0  420243.0    707       652.0   
2035  198507          3  471852  432599.0  511105.0    855       784.0   
2036  198506          3  565825  518011.0  613639.0   1026       939.0   
2037  198505          3  637302  592795.0  681809.0   1155      1074.0   
2038  198504          3  424937  390794.0  459080.0    770       708.0   
2039  198503          3  213901  174689.0  253113.0    388       317.0   
2040  198502          3   97586   80949.0  114223.0    177       147.0   
2041  198501          3   85489   65918.0  105060.0    155       120.0   
2042  198452          3   84830   60602.0  109058.0    154       110.0   
2043  198451

Our dataset uses an uncommon encoding; the week number is attached
to the year number, leaving the impression of a six-digit integer.
That is how Pandas interprets it.

A second problem is that Pandas does not know about week numbers.
It needs to be given the dates of the beginning and end of the week.
We use the library `isoweek` for that.

Since the conversion is a bit lengthy, we write a small Python 
function for doing it. Then we apply it to all points in our dataset. 
The results go into a new column 'period'.

In [ ]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

There are two more small changes to make.

First, we define the observation periods as the new index of
our dataset. That turns it into a time series, which will be
convenient later on.

Second, we sort the points chronologically.

In [ ]:
sorted_data = data.set_index('period').sort_index()

We check the consistency of the data. Between the end of a period and
the beginning of the next one, the difference should be zero, or very small.
We tolerate an error of one second.

This is OK except for one pair of consecutive periods between which
a whole week is missing.

We recognize the dates: it's the week without observations that we
have deleted earlier!

In [ ]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

A first look at the data!

In [ ]:
sorted_data['inc'].plot()

A zoom on the last few years shows more clearly that the peaks are situated in winter.

In [ ]:
sorted_data['inc'][-200:].plot()

## Study of the annual incidence

Since the peaks of the epidemic happen in winter, near the transition
between calendar years, we define the reference period for the annual
incidence from August 1st of year $N$ to August 1st of year $N+1$. We
label this period as year $N+1$ because the peak is always located in
year $N+1$. The very low incidence in summer ensures that the arbitrariness
of the choice of reference period has no impact on our conclusions.

Our task is a bit complicated by the fact that a year does not have an
integer number of weeks. Therefore we modify our reference period a bit:
instead of August 1st, we use the first day of the week containing August 1st.

A final detail: the dataset starts in October 1984, the first peak is thus
incomplete, We start the analysis with the first full peak.

In [ ]:
first_august_week = [pd.Period(pd.Timestamp(y, 8, 1), 'W')
                     for y in range(1985,
                                    sorted_data.index[-1].year)]

Starting from this list of weeks that contain August 1st, we obtain intervals of approximately one year as the periods between two adjacent weeks in this list. We compute the sums of weekly incidences for all these periods.

We also check that our periods contain between 51 and 52 weeks, as a safeguard against potential mistakes in our code.

In [ ]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_august_week[:-1],
                        first_august_week[1:]):
    one_year = sorted_data['inc'][week1:week2-1]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)
yearly_incidence = pd.Series(data=yearly_incidence, index=year)

And here are the annual incidences.

In [ ]:
yearly_incidence.plot(style='*')

A sorted list makes it easier to find the highest values (at the end).

In [ ]:
yearly_incidence.sort_values()

Finally, a histogram clearly shows the few very strong epidemics, which affect about 10% of the French population,
but are rare: there were three of them in the course of 35 years. The typical epidemic affects only half as many people.

In [ ]:
yearly_incidence.hist(xrot=20)